In [1]:
import pandas as pd

In [2]:
seasons = [2024, 2023, 2022, 2021, 2020, 2019]
leagues_dictionary = {
    'MX1': 31,
    'BR1': 24,
    'ARG1': 21,
    'MLS': 22,
    'ENG1': 9,
    'ESP1': 12,
    'ITA1': 11,
    'GER1': 20,
    'FRA1': 13,
    'HOL1': 23,
    'POR1': 32,
    'ENG2': 10

}

df_sum = pd.DataFrame()
df_def = pd.DataFrame()

for league, code in leagues_dictionary.items():
    for season in seasons:
        sum_temp = pd.read_parquet("Data/{}/{}_{}_Sum.gzip".format(league, league, season))
        def_temp = pd.read_parquet("Data/{}/{}_{}_Def.gzip".format(league, league, season))
        sum_temp['league'], def_temp['league'], sum_temp['code'], def_temp['code'], sum_temp['season'], def_temp['season'] = league, league, code, code, season, season

        df_sum = pd.concat([df_sum, sum_temp])
        df_def = pd.concat([df_def, def_temp])  
        
        
df_sum['team'] = df_sum['team'] + df_sum.league
df_def['team'] = df_def['team'] + df_def.league

df_sum['key'] = df_sum['match'] + "|" + df_sum["team"] + "|" + df_sum['rival'] + "|" + df_sum['league']
        


In [3]:
match_list = df_sum.groupby(['match']).agg(
    winner=('winner', 'first'),
    league=('league', 'first'),
    date=('date', 'first'),
    time=('time', 'first'),
    stadium=('stadium','first'),
    home_goals=('Gls', lambda x: x[df_sum['location'] == 'home'].sum() if 'home' in x.values else 0),
    away_goals=('Gls', lambda x: x[df_sum['location'] == 'away'].sum() if 'away' in x.values else 0),
    home_team=('team', 'first'),
    away_team=('team', 'last')
).reset_index()

In [4]:
home_list = df_sum[df_sum['location'] == "home"].groupby(['match']).agg(
    winner=('winner', 'first'),
    league=('league', 'first'),
    date=('date', 'first'),
    home_goals=('Gls', 'sum'),
    home_team=('team', 'first')
).reset_index()

away_list = df_sum[df_sum['location'] == "away"].groupby(['match']).agg(
    away_goals=('Gls', 'sum'),
    away_team=('team', 'first')
).reset_index()

In [5]:
away_list

match  away_goals      away_team
0         Ajaccio-Angers-2022-12-28         0.0     AngersFRA1
1        Ajaccio-Auxerre-2023-04-09         2.0    AuxerreFRA1
2          Ajaccio-Brest-2023-04-23         0.0      BrestFRA1
3       Ajaccio-Clermont-2022-10-02         2.0   ClermontFRA1
4           Ajaccio-Lens-2022-08-14         0.0       LensFRA1
...                             ...         ...            ...
20097  Wycombe-Rotherham-2020-09-12         1.0  RotherhamENG2
20098  Wycombe-Sheffield-2020-10-31         0.0  SheffieldENG2
20099      Wycombe-Stoke-2020-12-02         1.0      StokeENG2
20100    Wycombe-Swansea-2020-09-26         2.0    SwanseaENG2
20101    Wycombe-Watford-2020-10-27         1.0    WatfordENG2

[20102 rows x 3 columns]

In [6]:
match_list = home_list.merge(away_list, how='left', on="match")[['match', 'home_team', 'away_team', 'home_goals', 'away_goals', 'winner', 'date']]

In [7]:
match_list

match    home_team  ... winner        date
0         Ajaccio-Angers-2022-12-28  AjaccioFRA1  ...   home  2022-12-28
1        Ajaccio-Auxerre-2023-04-09  AjaccioFRA1  ...   away  2023-04-09
2          Ajaccio-Brest-2023-04-23  AjaccioFRA1  ...    tie  2023-04-23
3       Ajaccio-Clermont-2022-10-02  AjaccioFRA1  ...   away  2022-10-02
4           Ajaccio-Lens-2022-08-14  AjaccioFRA1  ...    tie  2022-08-14
...                             ...          ...  ...    ...         ...
20140  Wycombe-Rotherham-2020-09-12  WycombeENG2  ...   away  2020-09-12
20141  Wycombe-Sheffield-2020-10-31  WycombeENG2  ...   home  2020-10-31
20142      Wycombe-Stoke-2020-12-02  WycombeENG2  ...   away  2020-12-02
20143    Wycombe-Swansea-2020-09-26  WycombeENG2  ...   away  2020-09-26
20144    Wycombe-Watford-2020-10-27  WycombeENG2  ...    tie  2020-10-27

[20145 rows x 7 columns]

In [8]:
match_list

match    home_team  ... winner        date
0         Ajaccio-Angers-2022-12-28  AjaccioFRA1  ...   home  2022-12-28
1        Ajaccio-Auxerre-2023-04-09  AjaccioFRA1  ...   away  2023-04-09
2          Ajaccio-Brest-2023-04-23  AjaccioFRA1  ...    tie  2023-04-23
3       Ajaccio-Clermont-2022-10-02  AjaccioFRA1  ...   away  2022-10-02
4           Ajaccio-Lens-2022-08-14  AjaccioFRA1  ...    tie  2022-08-14
...                             ...          ...  ...    ...         ...
20140  Wycombe-Rotherham-2020-09-12  WycombeENG2  ...   away  2020-09-12
20141  Wycombe-Sheffield-2020-10-31  WycombeENG2  ...   home  2020-10-31
20142      Wycombe-Stoke-2020-12-02  WycombeENG2  ...   away  2020-12-02
20143    Wycombe-Swansea-2020-09-26  WycombeENG2  ...   away  2020-09-26
20144    Wycombe-Watford-2020-10-27  WycombeENG2  ...    tie  2020-10-27

[20145 rows x 7 columns]

In [9]:
import pandas as pd

match_df = pd.DataFrame()

def match_df_transform(row):
    global match_df
    home_row = {'team': row['home_team'], 'rival': row['away_team'], 'goals': row['home_goals'], 'rival_goals': row['away_goals'], 'date': row['date']}
    match_df = match_df.append(home_row, ignore_index=True)
    away_row = {'team': row['away_team'], 'rival': row['home_team'], 'goals': row['away_goals'], 'rival_goals': row['home_goals'], 'date': row['date']}
    match_df = match_df.append(away_row, ignore_index=True)

match_list.apply(match_df_transform, axis=1)

0        None
1        None
2        None
3        None
4        None
         ... 
20140    None
20141    None
20142    None
20143    None
20144    None
Length: 20145, dtype: object

In [10]:
match_df['elo'] = 100

In [11]:
match_df.sort_values(by='date', ascending=True, inplace=True)

In [12]:
match_df.columns

Index(['team', 'rival', 'goals', 'rival_goals', 'date', 'elo'], dtype='object')

In [13]:
import pandas as pd
import numpy as np

def calculate_elo(old_elo, goals, rival_goals, is_home):
    # Weight constants for different match types
    match_type_weights = {
        'World Cup finals': 60,
        'continental championship finals and major intercontinental tournaments': 50,
        'World Cup and continental qualifiers and major tournaments': 40,
        'all other tournaments': 30,
        'friendly matches': 20
    }

    # Assigning a default weight for all matches in your DataFrame
    match_weight = 20

    # K is the weight constant for the tournament played
    k = match_type_weights.get('all other tournaments', match_weight)

    # Adjust K based on goal difference
    goal_difference = abs(goals - rival_goals)
    if goal_difference == 2:
        k += k / 2
    elif goal_difference == 3:
        k += k * 3 / 4
    elif goal_difference >= 4:
        k += k * (3 / 4 + (goal_difference - 3) / 8)

    # W is the result of the game (1 for a win, 0.5 for a draw, and 0 for a loss)
    if goals > rival_goals:
        w = 1
    elif goals == rival_goals:
        w = 0.5
    else:
        w = 0

    # dr equals the difference in ratings plus 100 points for a team playing at home
    dr = old_elo + (100 if is_home else 0)

    # We is the expected result (win expectancy)
    we = 1 / (10**(-dr/400) + 1)

    # Rn = Ro + K × (W - We)
    new_elo = old_elo + k * (w - we)

    return new_elo

In [14]:
def get_new_elo(row):
    date = row['date']
    
    # Filtrar partidos anteriores a la fecha actual
    previous_matches = match_df[match_df['date'] < date].sort_values(by="date", ascending=True)
    
    if not previous_matches.empty:
        # Obtener el Elo más reciente antes del partido actual
        old_elo = previous_matches.tail(1)['elo'].values[0]
        
        # Calcular el nuevo Elo utilizando la función calculate_elo
        new_elo = calculate_elo(old_elo, row['goals'], row['rival_goals'], True)
        
        return new_elo
    else:
        # Si no hay partidos anteriores, devolver el Elo actual
        return row['elo']

# Aplicar la función get_new_elo a cada fila del DataFrame
match_df['elo'] = match_df.apply(get_new_elo, axis=1)

In [16]:
match_df

team          rival  goals  rival_goals        date         elo
2419    QuerétaroMX1       AtlasMX1    0.0          0.0  2018-07-20  100.000000
2418        AtlasMX1   QuerétaroMX1    0.0          0.0  2018-07-20  100.000000
38303        UNAMMX1    VeracruzMX1    2.0          0.0  2018-07-20  100.000000
38302    VeracruzMX1        UNAMMX1    0.0          2.0  2018-07-20  100.000000
36867        LeónMX1        UANLMX1    0.0          2.0  2018-07-21   65.811388
...              ...            ...    ...          ...         ...         ...
16256    GranadaESP1   AtléticoESP1    0.0          1.0  2024-01-22   77.207592
19880  LeicesterENG2    IpswichENG2    0.0          1.0  2024-01-22   77.207592
7306    BrightonENG1     WolvesENG1    0.0          0.0  2024-01-22   92.207592
7307      WolvesENG1   BrightonENG1    0.0          0.0  2024-01-22   92.207592
19881    IpswichENG2  LeicesterENG2    1.0          0.0  2024-01-22  107.207592

[40290 rows x 6 columns]